<a href="https://colab.research.google.com/github/DEli-26/DS_Practicum/blob/main/class_toxic_text_BERT/deli_proj_pract_13_v2_0.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<font size=6><b>**Я.Практикум. Проект №13**</b></font>
    
<font size=6><b>**Проект для «Викишоп» с BERT**</b></font>

***

# Постановка задачи

**Заказчик**  
Интернет-магазин «Викишоп»

**Цель**  
Разработать модель машинного обучения, которая будет искать токсичные комментарии и отправлять их на модерацию.
В качестве метрики качества следует использовать F1, значение которой должно быть не менее 0,75.

**Задачи**  

1. Загрузить и исследовать данные;
1. Подготовить три вида признаков:
    - очищенный незакодированный текст;
    - TF-IDF;
    - emedings при помощи модели BERT; 
1. Обучить на полученных признаках модель логистической регрессии (LR);
1. Обучить на очищенном тексте модель CatBoost (CB) классифицировать позитивные и негативные комментарии на разных признаках;
1. Используя метрику ROC-AUC определить лучшее сочетание модели и признаков;
1. Для лучшей модели выбрать оптимальный порог (threshold) по критерию максимизации значения метрики F1;  
1. Сделать выводы.

**Исходные данные**  
Набор данных с разметкой о токсичности правок.

# Подготовка окружения

Загрузим библиотеки, необходимые для выполнения проекта

In [ ]:
import numpy as np
import pandas as pd
import nltk
import re

from nltk.corpus import stopwords as nltk_stopwords
from nltk.stem import PorterStemmer
from nltk.tokenize import word_tokenize
from pymystem3 import Mystem
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import f1_score, roc_auc_score
from sklearn.model_selection import (
    train_test_split,
    RandomizedSearchCV,
    StratifiedKFold,
)
from tqdm.notebook import tqdm

try:
    from catboost import CatBoostClassifier, Pool, cv
except:
    !pip install catboost
    from catboost import CatBoostClassifier, Pool, cv

try:
    import torch
except:
    !pip install torch
    import torch

try:
    import transformers
except:
    !pip install transformers
    import transformers


nltk.download("punkt")
nltk.download("stopwords")

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 76.6 MB 78 kB/s 
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 4.7 MB 16.6 MB/s 
     |████████████████████████████████| 6.6 MB 38.8 MB/s 
     |████████████████████████████████| 101 kB 624 kB/s 
     |████████████████████████████████| 596 kB 57.0 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

Загрузим сами данные.

In [ ]:
! gdown 1H8CdcOmEiXY_qDArpSs8QceSVxriGcQo

Downloading...
From: https://drive.google.com/uc?id=1H8CdcOmEiXY_qDArpSs8QceSVxriGcQo
To: /content/toxic_comments.csv
100% 64.1M/64.1M [00:01<00:00, 55.3MB/s]


In [ ]:
df = pd.read_csv("/content/toxic_comments.csv")

# Обзор данных

Вызовем первые 5 строк, общую информацию о таблице, а также количество дубликатов.

In [ ]:
df.head()

text  toxic
0  Explanation\nWhy the edits made under my usern...      0
1  D'aww! He matches this background colour I'm s...      0
2  Hey man, I'm really not trying to edit war. It...      0
3  "\nMore\nI can't make any real suggestions on ...      0
4  You, sir, are my hero. Any chance you remember...      0

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 159571 entries, 0 to 159570
Data columns (total 2 columns):
 #   Column  Non-Null Count   Dtype 
---  ------  --------------   ----- 
 0   text    159571 non-null  object
 1   toxic   159571 non-null  int64 
dtypes: int64(1), object(1)
memory usage: 2.4+ MB


In [ ]:
df.duplicated().sum()

0

Датафрейм содержит 159 571 объекта без пропусков и явных повторений.
Каждый объект включает текст комментария `text` и целевой признак `toxic`.
При этом, комментарии сделаны на английском языке.

Проверим дисбаланс классов.

In [ ]:
df["toxic"].mean()

0.10167887648758234

Только 10% данных содержат токсичные комментарии.
Такой дисбаланс должен быть учтен при разбиении датафрема на обучающую и тестовую выборки.

Рассмотрим детально первую строку с текстом.

In [ ]:
df["text"][0]

"Explanation\nWhy the edits made under my username Hardcore Metallica Fan were reverted? They weren't vandalisms, just closure on some GAs after I voted at New York Dolls FAC. And please don't remove the template from the talk page since I'm retired now.89.205.38.27"

Текстовая информация содержит следующие особенности:  
* используется различный регистр;
* используются скрытые текстовые символы (\n, \t...);
* используются числовые символы;
* используется различная форма слов.

Для улучшения значения целевой метрики при подготовке признаков перечисленные недостатки целесообразно устранить.

# Подготовка признаков

## Очистка текста

Проведем обработку строк: очистим их от лишних символов и стоп-слов.

In [ ]:
stopwords = set(nltk_stopwords.words("english"))

In [ ]:
def clear(raw):
    text = raw["text"].lower()
    text = " ".join(re.sub(r"[^a-zA-Z ]", " ", text).split())
    text = " ".join([w for w in word_tokenize(text) if not w in stopwords])
    return text

In [ ]:
df["text"] = df.apply(clear, axis=1)

Проверим выполнение операции

In [ ]:
df["text"][0]

'explanation edits made username hardcore metallica fan reverted vandalisms closure gas voted new york dolls fac please remove template talk page since retired'

Очистка выполнена.
Однако при этом могли проявится дубликаты в данных, которые были неявными при первоначальном обзоре.

In [ ]:
df.duplicated().sum()

1791

Количество таких дубликатов составляет около 1%, в результате чего они могут быть безболезненно удалены.

In [ ]:
df = df.drop_duplicates().reset_index(drop=True)

In [ ]:
df.duplicated().sum()

0

Признак с очищенным текстом сформирован, можно переходить к следующему шагу.

## Stemming

Выполним stemming по алгоритму Портера.
Полученный указанной обработкой корпус слов сохраним в соответствующий столбец.

Для повышения стабильности обработки добавим заполнение корпуса пропуском в случае, если не удается выполнить stemming.

In [ ]:
porter = PorterStemmer()

In [ ]:
def porterstem(raw):
    text = raw["text"]
    try:
        text = " ".join([porter.stem(word) for word in text.split()])
    except:
        text = np.NaN
    return text

In [ ]:
def encoder(feature_name, batch_size, function_name):
    df[feature_name] = np.NaN
    for i in tqdm(range(df.shape[0] // batch_size)):
        df[feature_name][batch_size * i : batch_size * (i + 1)] = df[
            batch_size * i : batch_size * (i + 1)
        ].apply(function_name, axis=1)

    df[feature_name][batch_size * (i + 1) :] = df[batch_size * (i + 1) :].apply(
        function_name, axis=1
    )

In [ ]:
encoder("corpus", 10000, porterstem)

  0%|          | 0/15 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


Проверим количество пропусков.

In [ ]:
df.isna().sum()

text      0
toxic     0
corpus    1
dtype: int64

Один объект не обработался. 
Выведем строку с ним и содержимое ячейки с комментарием.

In [ ]:
df.loc[df["corpus"].isna()]

text  toxic corpus
114502  feel might cyber apocalypse yyyyyyyyyyyyyyybvg...      0    NaN

In [ ]:
df.loc[df["corpus"].isna()]["text"].values

array(['feel might cyber apocalypse yyyyyyyyyyyyyyybvgtfrrrrrbyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyyy

По всей видимости, объект - шутка разработчиков задачи.
Учитывая, что он не несет смысловой нагрузки, исключим его из рассмотрения. 

In [ ]:
df.dropna(inplace=True)
df.reset_index(inplace=True)

Полученный stemming'ом корпус слов используем при определении TF-IDF.
Учитывая, что указанный параметр зависит от состава выборки, его определение целесообразно проводить только после разделения датафрейма на обучающую, валидационную и тестовую выборки.

## Embeding

Инициализируем токенизатор и модель BERT на основе базовой предобученной из стандартной библиотеки.

In [ ]:
tokenizer = transformers.DistilBertTokenizer.from_pretrained("distilbert-base-uncased")
model_bert = transformers.DistilBertModel.from_pretrained("distilbert-base-uncased")

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertModel: ['vocab_transform.weight', 'vocab_projector.bias', 'vocab_transform.bias', 'vocab_layer_norm.weight', 'vocab_layer_norm.bias', 'vocab_projector.weight']
- This IS expected if you are initializing DistilBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


Преобразуем текст в номера токенов из словаря методом encode.
Учитывая, что выбранная модель BERT предобучена на текстах длинной 512 слов, добавим соответствующий параметр в метод encode.

In [ ]:
def bert_token(raw):
    text = raw["text"]
    try:
        text = tokenizer.encode(text, add_special_tokens=True, max_length=512)
    except:
        text = np.NaN
    return text

In [ ]:
encoder("corpus_bert", 10000, bert_token)

  0%|          | 0/15 [00:00<?, ?it/s]

Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


Проверим количество пропущенных объектов.

In [ ]:
df.isna().sum()

index          0
text           0
toxic          0
corpus         0
corpus_bert    0
dtype: int64

Для всех объектов успешно созданы токены.

Применим метод padding, чтобы уравнять длины исходных текстов в корпусе. 

In [ ]:
padded = np.array([i + [0] * (512 - len(i)) for i in df["corpus_bert"].values])

Отбросим нулевые токены и создадим attention_mask для действительно важных из них. 

In [ ]:
attention_mask = np.where(padded != 0, 1, 0)

Определим сами embedings.

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")


def batch_embeder(low_step, high_step):
    # преобразуем данные
    batch = torch.tensor(padded[low_step:high_step]).to(device)
    # преобразуем маску
    attention_mask_batch = torch.tensor(attention_mask[low_step:high_step]).to(device)

    with torch.no_grad():
        model_bert.to(device)
        batch_embeddings = model_bert(batch, attention_mask=attention_mask_batch)

    # преобразуем элементы методом numpy() к типу numpy.array
    return batch_embeddings[0][:, 0, :].cpu().numpy()

In [ ]:
embeddings = []
batch_size = 50

for i in tqdm(range(padded.shape[0] // batch_size)):
    embeddings.append(batch_embeder(batch_size * i, batch_size * (i + 1)))

# финальный проход
embeddings.append(batch_embeder(batch_size * (i + 1), None))

  0%|          | 0/3155 [00:00<?, ?it/s]

Соберём все embedings в матрицу признаков вызовом функции concatenate():

In [ ]:
features_bert = np.concatenate(embeddings)

Embedings созданы.
Можно переходить к разделению датафрейма на подвыборки.

## Разделение на подвыборки

Разделим данные на подвыборки в пропорции 3:1:1 с сохранением дисбаланса классов.

In [ ]:
train_features_bert, val_test_features_bert, train, val_test = train_test_split(
    features_bert, df, test_size=0.4, random_state=26, stratify=df["toxic"]
)

val_features_bert, test_features_bert, val, test = train_test_split(
    val_test_features_bert,
    val_test,
    test_size=0.5,
    random_state=26,
    stratify=val_test["toxic"],
)

In [ ]:
train["toxic"].mean(), val["toxic"].mean(), test["toxic"].mean()

(0.1016616138675568, 0.10166053999239448, 0.10166053999239448)

Дисбаланс сохранен.

Теперь необходимо сформировать значения TF-IDF корпуса текстов.
Для выполнения вычислений используем соответствующую библиотеку. 

In [ ]:
count_tf_idf = TfidfVectorizer(stop_words=stopwords)

train_tf_idf = count_tf_idf.fit_transform(train["corpus"])
val_tf_idf = count_tf_idf.transform(val["corpus"])
test_tf_idf = count_tf_idf.transform(test["corpus"])

Признаки TF-IDF сформированы, можно приступать к моделированию.

# Моделирование

## Логистическая регрессия

Определим модель и проведем ее обучение на двух типах признаков: TF-IDF и BERT embedings.

Одним из ключевых гиперпараметров LR является вес классов.
В этой связи проведем его подбор при помощи метода случайного поиска.

In [ ]:
parameters = {"C": np.linspace(0.0001, 100, 20)}
skf = StratifiedKFold(5, shuffle=True, random_state=26)

In [ ]:
model_lr_tf_idf = RandomizedSearchCV(
    estimator=LogisticRegression(max_iter=500, random_state=26, n_jobs=-1),
    param_distributions=parameters,
    n_jobs=-1,
    n_iter=5,
    random_state=26,
)
model_lr_tf_idf.fit(train_tf_idf, train["toxic"])

RandomizedSearchCV(estimator=LogisticRegression(max_iter=500, n_jobs=-1,
                                                random_state=26),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'C': array([1.00000000e-04, 5.26325263e+00, 1.05264053e+01, 1.57895579e+01,
       2.10527105e+01, 2.63158632e+01, 3.15790158e+01, 3.68421684e+01,
       4.21053211e+01, 4.73684737e+01, 5.26316263e+01, 5.78947789e+01,
       6.31579316e+01, 6.84210842e+01, 7.36842368e+01, 7.89473895e+01,
       8.42105421e+01, 8.94736947e+01, 9.47368474e+01, 1.00000000e+02])},
                   random_state=26)

In [ ]:
model_lr_bert = RandomizedSearchCV(
    estimator=LogisticRegression(max_iter=500, random_state=26, n_jobs=-1),
    param_distributions=parameters,
    n_jobs=-1,
    cv=skf,
    n_iter=5,
    random_state=26,
)
model_lr_bert.fit(train_features_bert, train["toxic"])

/usr/local/lib/python3.7/dist-packages/joblib/externals/loky/process_executor.py:705: UserWarning: A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.
  "timeout or by a memory leak.", UserWarning


RandomizedSearchCV(cv=StratifiedKFold(n_splits=5, random_state=26, shuffle=True),
                   estimator=LogisticRegression(max_iter=500, n_jobs=-1,
                                                random_state=26),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'C': array([1.00000000e-04, 5.26325263e+00, 1.05264053e+01, 1.57895579e+01,
       2.10527105e+01, 2.63158632e+01, 3.15790158e+01, 3.68421684e+01,
       4.21053211e+01, 4.73684737e+01, 5.26316263e+01, 5.78947789e+01,
       6.31579316e+01, 6.84210842e+01, 7.36842368e+01, 7.89473895e+01,
       8.42105421e+01, 8.94736947e+01, 9.47368474e+01, 1.00000000e+02])},
                   random_state=26)

Определим значение метрики ROC-AUC на валидационной подвыборке.
Указанная метрика не зависит от порога для предсказания класса, в связи с чем ее целесообразно использовать для сравнения разных моделей и определения лучшей из них.

In [ ]:
roc_auc_score(val["toxic"], model_lr_tf_idf.predict(val_tf_idf))

0.8455538520708247

In [ ]:
roc_auc_score(val["toxic"], model_lr_bert.predict(val_features_bert))

0.8085209976680987

По полученным значениям видно, что обучение LR на признаках TF-IDF на 3,7% эффективнее обучения на embedings.

Проверим качество обучение модели CB.

## Catboost

Модель CB имеет встроенные механизмы формирования embedings.
В этой связи ей достаточно передать только очищенный текст, обозначив его соответствующим образом.

In [ ]:
train_pool = Pool(
    data=train[["corpus"]],
    label=train["toxic"],
    feature_names=["corpus"],
    text_features=["corpus"],
)

val_pool = Pool(
    data=val[["corpus"]],
    label=val["toxic"],
    feature_names=["corpus"],
    text_features=["corpus"],
)

Обучение модели СВ проведем при помощи встроенного метода кросс-валидации.

In [ ]:
%%time 
params = {
    "eval_metric": "Logloss",
    "loss_function": "Logloss",
    "learning_rate": 0.1,
    "random_seed": 26,
    "verbose": 250,
    'early_stopping_rounds':200,
}

cv_data = cv(
    pool=train_pool,
    params=params,
    fold_count=5,
    shuffle=True,
    partition_random_seed=0,
    stratified=True,
    verbose=False,
    early_stopping_rounds=200,
    return_models=True,
    plot=True,
)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Training on fold [0/5]

bestTest = 0.1178600531
bestIteration = 795

Training on fold [1/5]

bestTest = 0.1210751819
bestIteration = 970

Training on fold [2/5]

bestTest = 0.1157529758
bestIteration = 917

Training on fold [3/5]

bestTest = 0.1138300644
bestIteration = 922

Training on fold [4/5]

bestTest = 0.1176687315
bestIteration = 807

CPU times: user 42min 14s, sys: 5min 19s, total: 47min 34s
Wall time: 26min 45s


Лучшая модель получена на фолде с номером 3.
Определим для нее метрику ROC-AUC.

In [ ]:
roc_auc_score(val["toxic"], cv_data[1][3].predict(val_pool, prediction_type="Class"))

0.8386337361408107

Полученное значение на 0,7% хуже соответствующего, полученного при обучении модели LR на признаках TF-IDF.
В этой связи, для полноценного сравнения проведем аналогичное обучение на тех же признаках.

In [ ]:
train_pool_tf_idf = Pool(
    data=train_tf_idf,
    label=train["toxic"],
)

val_pool_tf_idf = Pool(
    data=val_tf_idf,
    label=val["toxic"],
)

In [ ]:
%%time 
cv_data_tf_idf = cv(
    pool=train_pool_tf_idf,
    params=params,
    fold_count=5,
    shuffle=True,
    partition_random_seed=0,
    stratified=True,
    verbose=False,
    early_stopping_rounds=200,
    return_models=True,
    plot=True,
)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Training on fold [0/5]

bestTest = 0.1289406661
bestIteration = 998

Training on fold [1/5]

bestTest = 0.1299653644
bestIteration = 995

Training on fold [2/5]

bestTest = 0.1328813175
bestIteration = 998

Training on fold [3/5]

bestTest = 0.1255856161
bestIteration = 998

Training on fold [4/5]

bestTest = 0.1289961322
bestIteration = 997

CPU times: user 3h 9min 36s, sys: 2min 8s, total: 3h 11min 45s
Wall time: 1h 48min 14s


In [ ]:
roc_auc_score(
    val["toxic"], cv_data_tf_idf[1][0].predict(val_pool_tf_idf, prediction_type="Class")
)

0.815842145553289

Полученное значение хуже полученного при кодировании текста внутренними средствами модели CB.

Таким образом, по метрике ROC-AUC на валидационной выборке лучшей из рассмотренных моделей, является модель LR, обученная на признаках TF-IDF.

На следующем шаге определим лучшее значение порога для расчета целевой метрики F1.

## Выбор порога классификации

Определим значение целевой метрики со стандартным порогом, равным 0,5. 

In [ ]:
f1_score(val["toxic"], model_lr_tf_idf.predict(val_tf_idf))

0.7710925515595705

Полученное значение выше заданного по условиям задачи критерия 0,75. 
Учитывая, что на тестовой выборке указанная метрика, скорее всего, изменится в худшую сторону, целесообразно провести анализ  возможности ее улучшения за счет изменения порога классификации.
Для этого создадим столбец со значениями вероятности определения к тому или иному классу.

In [ ]:
val["pred_lr_tf_idf_proba"] = np.NaN
val["pred_lr_tf_idf_proba"] = 1 - model_lr_tf_idf.predict_proba(val_tf_idf)

Определим перечень всех существующих значений вероятностей и добавим его к нулевому значению.

In [ ]:
thrs = [0] + list(val["pred_lr_tf_idf_proba"].unique())

Переберем в цикле значения метрики F1 при изменении порога по всем значениям вероятности.

In [ ]:
result = []

for thr in tqdm(thrs):
    val["pred_lr_tf_idf_best"] = (val["pred_lr_tf_idf_proba"] > thr) * 1
    result.append((thr, f1_score(val["toxic"], val["pred_lr_tf_idf_best"])))

  0%|          | 0/31394 [00:00<?, ?it/s]

Выведем значение порога, обеспечивающего получение максимальное значение целевой метрики. 

In [ ]:
t = pd.DataFrame(result, columns=["thr", "f1"])

thr_best = t.loc[t["f1"] == t["f1"].max(), "thr"].values[0]

t[t["f1"] == t["f1"].max()]

thr        f1
209  0.415595  0.776638

Полученное значение лучше "ненастроенного" на 0,5%.

В дальнейшем будем использовать его для расчета целевой метрики на тестовой подвыборке.

## Тестирование лучшей модели

Проведем расчет целевой метрики F1 на тестовой подвыборке.

In [ ]:
test["pred_lr_tf_idf_proba"] = np.NaN
test["pred_lr_tf_idf_proba"] = 1 - model_lr_tf_idf.predict_proba(test_tf_idf)
test["pred_lr_tf_idf_best"] = (test["pred_lr_tf_idf_proba"] > thr_best) * 1
f1_score(test["toxic"], test["pred_lr_tf_idf_best"])

0.77541604877245

Полученное значение выше заданного в условии задания на 2,5%.

# Выводы

Для достижения поставленной условием задания цели решены следующие задачи:
1. Загружены и исследованы данные;
1. Проведена очистка незакодированного текста от лишних символов и стоп-слов;
1. Определены признаки TF-IDF;
1. Сформированы emedings при помощи предобученной модели BERT из стандартной библиотеки "distilbert-base-uncased"; 
1. Обучены на полученных признаках модели логистической регрессии (LR) и CatBoost (CB);
1. Использована метрика ROC-AUC для определения лучшего сочетание модели и признаков. 
Получено, что для обученной на признаках TF-IDF модели LR указанная метрика имеет наивысшее значение, равное 84,5%;
1. Для указанной модели выбран порог, обеспечивающий максимизацию значения метрики F1. 

В результате работы разработана модель LR, определяющая токсичные комментарии, со значением метрики F1, равным 77,5%, что лучше заданного в условии порога на 2,5%.
Разработанная модель может быть использована для отправки токсичных комментариев на модерацию.